In [7]:
from pls_filter import *
from customfunctions import *
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

if __name__=="__main__":
    main=pd.read_csv('data/trans1/defense.csv')
    main=main.fillna(0)
    mapdoc=pd.read_excel('data/mapping/team_map.xlsx')
    mapdic={}
    for idx, row in mapdoc.iterrows():
        mapdic[row['oddsteams']]=row['nflscrapr']
    odds=pd.read_excel('data/odds/nfl.xlsx')
    odds['Home Team']=odds['Home Team'].map(mapdic)
    odds['Away Team']=odds['Away Team'].map(mapdic)
    strts=pd.to_datetime(['2009-09-10','2010-09-09','2011-09-08','2012-09-05','2013-09-05','2014-09-04','2015-09-10','2016-09-08','2017-09-07','2018-09-06','2019-09-05','2020-09-05'], format='%Y-%m-%d')
    yrs=[2009,2010,2011,2012,2013,2014,2015,2016,2017,2018,2019]
    bins=pd.IntervalIndex.from_tuples([(strts[i],strts[i+1]) for i in range(len(strts)-1)], closed='left')
    odds['Date'] = pd.to_datetime(odds['Date'], format='%Y-%m-%d')
    odds=odds[odds['Date']>='2009-09-10']
    odds['year']=pd.cut(odds['Date'],bins).map(dict(zip(bins,yrs))).astype(int)
    odds['ssn_start']=odds['year'].map(dict(zip(yrs,strts[:-1])))
    odds['week']=((odds['Date']-odds['ssn_start']).astype(str).str.split(" ", expand=True)[0].astype(int)//7)+1
    #print(mapdic)
    #print(odds)
    totp=0
    tota=0
    cap=0
    for yr in range(2017,2020):
        yrp=0
        for wk in range(1,18):
            wkp=0
            wka=0
            main1=main[((main['d_year']>=2011) & (main['d_year']<=yr-1))|((main['d_year']==yr) & (main['d_week']<wk))].reset_index()
            main2=main[((main['d_year']==yr) & (main['d_week']==wk))].reset_index()
            main3=odds[((odds['year']==yr) & (odds['week']==wk))].reset_index()
            main1.to_csv('data/trans2/deftrn.csv')
            main2.to_csv('data/trans2/deftst.csv')
            yskip=['pass_attempt','complete_pass','air_yards','yards_after_catch','pass_touchdown','complete_pass','air_yards','yards_after_catch','pass_touchdown','rush_attempt','yards_gained','rush_touchdown','sack','interception',
            'fumble_forced','qb_hit','return_touchdown''field_goal_attempt','fg','winpct','dif']
            skip=['o_'+col for col in yskip]
            skip+=['d_'+col for col in yskip]
            y=['d_dif']
            nstnd=['index','d_defteam','d_game_id','d_Game0','d_team','o_defteam','o_game_id','o_Game0','o_team','Unnamed: 0']
            x=[col for col in main.columns if (main[col].dtype==np.float64 or main[col].dtype==np.int64) and col not in nstnd and col not in skip and col not in y]
            #for inp in x:
                #print(inp)
            #stndf=STAND(main,main,stndcols)
            PLS_SAVE(5,'data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav')
            trn=PLS_LTRANS('data/trans2/deftrn.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftrn.csv')
            tst=PLS_LTRANS('data/trans2/deftst.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftst.csv')
            tmp={}
            for i in range(len(tst)):
                #print(main2)
                #print(main2.loc[i,'d_team'])
                tmp[main2.loc[i,'d_team']]=REG_FILT('data/plstrans/deftrn.csv','data/trans2/deftrn.csv',tst.loc[[i]],1000,None,2,write=False)
            #print(main2['d_team'].value_counts())
            for idx,row in main3.iterrows():
                #print(row)
                try:
                    homedist=tmp[row['Home Team']]
                    awaydist=tmp[row['Away Team']]
                    home_w_p=.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist)))
                    homeh_w_p=dectoprob(row['Home Odds Open'])
                    away_w_p=.5*((len(homedist[homedist['d_dif']<0])/len(homedist))+(len(awaydist[awaydist['d_dif']>0])/len(awaydist)))
                    awayh_w_p=dectoprob(row['Away Odds Open'])
                    lhome_w_p=.5*((len(homedist[homedist['d_dif']>row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']<row['Away Line Open']])/len(awaydist)))
                    lhomeh_w_p=dectoprob(row['Home Line Odds Open'])
                    laway_w_p=.5*((len(homedist[homedist['d_dif']<row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']>row['Away Line Open']])/len(awaydist)))
                    lawayh_w_p=dectoprob(row['Away Line Odds Open'])
                #print('ayy')
                #print(dectoprob(row['Home Odds Open']),.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))))
                    if dectoprob(row['Home Odds Open'])<.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))):
                        prob=dectoprob(row['Home Odds Open'])
                        #amt=-(cap/4)*(prob-.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))))
                        amt=simsharpe(100000,homeh_w_p,home_w_p)[2]                        
                        win=row['Home Score']>row['Away Score']
                        print('a',row,prob,amt,betprofit(amt,prob,win))
                        wkp+=betprofit(amt,prob,win)
                        wka+=amt
                    if dectoprob(row['Away Odds Open'])<.5*((len(homedist[homedist['d_dif']<0])/len(homedist))+(len(awaydist[awaydist['d_dif']>0])/len(awaydist))):
                        prob=dectoprob(row['Away Odds Open'])
                        #amt=-(cap/4)*(prob-.5*((len(homedist[homedist['d_dif']<0])/len(homedist))+(len(awaydist[awaydist['d_dif']>0])/len(awaydist))))
                        amt=simsharpe(100000,awayh_w_p,away_w_p)[2]                        
                        win=row['Home Score']<row['Away Score']
                        print('b',row,prob,amt,betprofit(amt,prob,win))
                        wkp+=betprofit(amt,prob,win)
                        wka+=amt
                    if dectoprob(row['Home Line Odds Open'])<.5*((len(homedist[homedist['d_dif']>row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']<-row['Away Line Open']])/len(awaydist))):
                        prob=dectoprob(row['Home Line Odds Open'])
                        #amt=-(cap/4)*(prob-.5*((len(homedist[homedist['d_dif']>row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']<row['Away Line Open']])/len(awaydist))))
                        amt=simsharpe(100000,lhomeh_w_p,lhome_w_p)[2]                        
                        win=row['Home Score']+row['Away Line Open']>row['Away Score']
                        print('c',row,prob,amt,betprofit(amt,prob,win))
                        wkp+=betprofit(amt,prob,win)
                        wka+=amt
                    if dectoprob(row['Away Line Odds Open'])<.5*((len(homedist[homedist['d_dif']<row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']>-row['Away Line Open']])/len(awaydist))):
                        prob=dectoprob(row['Away Line Odds Open'])
                        #amt=-(cap/4)*(prob-.5*((len(homedist[homedist['d_dif']<row['Away Line Open']])/len(homedist))+(len(awaydist[awaydist['d_dif']>row['Away Line Open']])/len(awaydist))))
                        amt=simsharpe(100000,lawayh_w_p,laway_w_p)[2]                        
                        win=row['Home Score']-row['Away Line Open']<row['Away Score']
                        print('d',row,prob,amt,betprofit(amt,prob,win))
                        wkp+=betprofit(amt,prob,win)
                        wka+=amt
                except Exception as e:
                    print(e)
                    #print(new['d_dif'].mean(),new['d_dif'].std())
                    #print(main2.loc[[i]][['d_dif','o_team','d_team','o_winpct','d_winpct','d_year','d_week']])
                #new['d_dif'].hist()
                #plt.savefig("plot{0}.pdf".format(str(i)))
                #plt.close()
            print(yr,wk,wkp,'wkprof')
            print(yr,wk,wkp/wka,'wkret')
            cap+=wkp
            print(yr,wk,cap/1000,cap,'netret')
            #totp+=wkp
            #tota+=wka
            #print(yr,wk,totp,'totprof')
            #print(yr,wk,totp/tota,'totret')
        #print(yr,yrp)
        #totp+=yrp
        #print('cum',totp)


/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


c index                                      711
Date                       2017-09-11 00:00:00
Home Team                                  DEN
Away Team                                  LAC
Home Score                                  24
Away Score                                  21
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                           1.561
Home Odds Min                            1.561
Home Odds Max                            1.714
Home Odds Close                          1.689
Away Odds Open                             2.6
Away Odds Min                             2.27
Away Odds Max                              2.6
Away Odds Close                           2.31
Home Line Open                            -3.5
Home Line Min                             -3.5
Home Line Max                               -3
Home Line Close                             -3
Away Line O

d index                                      714
Date                       2017-09-10 00:00:00
Home Team                                   GB
Away Team                                  SEA
Home Score                                  17
Away Score                                   9
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                           1.606
Home Odds Min                            1.606
Home Odds Max                            1.751
Home Odds Close                          1.724
Away Odds Open                            2.49
Away Odds Min                              2.2
Away Odds Max                             2.49
Away Odds Close                           2.25
Home Line Open                              -3
Home Line Min                               -3
Home Line Max                             -2.5
Home Line Close                           -2.5
Away Line O

d index                                      717
Date                       2017-09-10 00:00:00
Home Team                                  BUF
Away Team                                  NYJ
Home Score                                  21
Away Score                                  12
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                           1.259
Home Odds Min                             1.25
Home Odds Max                            1.303
Home Odds Close                          1.303
Away Odds Open                            4.34
Away Odds Min                             3.89
Away Odds Max                             4.46
Away Odds Close                           3.89
Home Line Open                              -7
Home Line Min                              -10
Home Line Max                             -6.5
Home Line Close                             -7
Away Line O

c index                                      720
Date                       2017-09-10 00:00:00
Home Team                                  CLE
Away Team                                  PIT
Home Score                                  18
Away Score                                  21
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                            4.69
Home Odds Min                             4.24
Home Odds Max                             4.73
Home Odds Close                           4.73
Away Odds Open                           1.232
Away Odds Min                            1.229
Away Odds Max                            1.268
Away Odds Close                          1.229
Home Line Open                               9
Home Line Min                                8
Home Line Max                               10
Home Line Close                             10
Away Line O

...

a index                                       11
Date                       2019-12-01 00:00:00
Home Team                                  NYG
Away Team                                   GB
Home Score                                  13
Away Score                                  31
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                            3.45
Home Odds Min                             3.25
Home Odds Max                              3.6
Home Odds Close                            3.6
Away Odds Open                            1.32
Away Odds Min                             1.31
Away Odds Max                             1.36
Away Odds Close                           1.31
Home Line Open                             6.5
Home Line Min                                6
Home Line Max                              6.5
Home Line Close                            6.5
Away Line O

a index                                       13
Date                       2019-11-28 00:00:00
Home Team                                  ATL
Away Team                                   NO
Home Score                                  18
Away Score                                  26
Overtime?                                  NaN
Playoff Game?                              NaN
Neutral Venue?                             NaN
Home Odds Open                            3.45
Home Odds Min                             3.45
Home Odds Max                              3.7
Home Odds Close                            3.7
Away Odds Open                            1.32
Away Odds Min                             1.29
Away Odds Max                             1.32
Away Odds Close                           1.29
Home Line Open                             6.5
Home Line Min                              6.5
Home Line Max                                7
Home Line Close                              7
Away Line O

/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


2019 14 0 wkprof


ZeroDivisionError: division by zero

In [11]:
import scipy

In [27]:
sd=13
scipy.stats.norm(9.5, sd).cdf(15.5)-scipy.stats.norm(9.5, sd).cdf(12.5)

0.08654087629678464

In [28]:
1/2.7-1/3.75
1/2.2-1/2.7
1.65/2.65-1/2.2
1/2.25-1/2.7
1/2.7-1/3.5
1/3.5

0.2857142857142857

In [39]:
float('+50')

50.0

In [42]:
a='po'
b=[x for x in ('po','mo') if x!=a][0]
b

'mo'

In [1]:
from pls_filter import *
from customfunctions import *
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

if __name__=="__main__":
    main=pd.read_csv('data/trans1/defense.csv')
    main=main.fillna(0)
    mapdoc=pd.read_excel('data/mapping/team_map.xlsx')
    mapdic={}
    for idx, row in mapdoc.iterrows():
        mapdic[row['oddsteams']]=row['nflscrapr']
    odds=pd.read_csv('data/odds/wk16odds.csv', dtype=str)
    strts=pd.to_datetime(['2009-09-10','2010-09-09','2011-09-08','2012-09-05','2013-09-05','2014-09-04','2015-09-10','2016-09-08','2017-09-07','2018-09-06','2019-09-05','2020-09-05'], format='%Y-%m-%d')
    yrs=[2009,2010,2011,2012,2013,2014,2015,2016,2017,2018,2019]
    bins=pd.IntervalIndex.from_tuples([(strts[i],strts[i+1]) for i in range(len(strts)-1)], closed='left')
    odds['date'] = pd.to_datetime(odds['date'], format='%Y-%m-%d')
    odds=odds[odds['date']>='2009-09-10']
    odds['year']=pd.cut(odds['date'],bins).map(dict(zip(bins,yrs))).astype(int)
    odds['ssn_start']=odds['year'].map(dict(zip(yrs,strts[:-1])))
    odds['week']=((odds['date']-odds['ssn_start']).astype(str).str.split(" ", expand=True)[0].astype(int)//7)+1
    #print(mapdic)
    print(odds)
    totp=0
    tota=0
    cap=1000
    yr=2019
    wk=16
    yrp=0
    wkp=0
    wka=0
    main1=main[((main['d_year']>=2011) & (main['d_year']<=yr-1))|((main['d_year']==yr) & (main['d_week']<wk))].reset_index()
    main2=main[((main['d_year']==yr) & (main['d_week']==wk))].reset_index()
    #print(main2)
    main3=odds[((odds['year']==yr) & (odds['week']==wk))].reset_index()
    #print(main3)
    main1.to_csv('data/trans2/deftrn.csv')
    main2.to_csv('data/trans2/deftst.csv')
    yskip=['pass_attempt','complete_pass','air_yards','yards_after_catch','pass_touchdown','complete_pass','air_yards','yards_after_catch','pass_touchdown','rush_attempt','yards_gained','rush_touchdown','sack','interception',
        'fumble_forced','qb_hit','return_touchdown''field_goal_attempt','fg','winpct','dif']
    skip=['o_'+col for col in yskip]
    skip+=['d_'+col for col in yskip]
    y=['d_dif']
    nstnd=['index','d_defteam','d_game_id','d_Game0','d_team','o_defteam','o_game_id','o_Game0','o_team','Unnamed: 0']
    x=[col for col in main.columns if (main[col].dtype==np.float64 or main[col].dtype==np.int64) and col not in nstnd and col not in skip and col not in y]
    #for inp in x:
        #print(inp)
        #stndf=STAND(main,main,stndcols)
    PLS_SAVE(5,'data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav')
    trn=PLS_LTRANS('data/trans2/deftrn.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftrn.csv')
    tst=PLS_LTRANS('data/trans2/deftst.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftst.csv')
    tmp={}
    #print(tst)
    for i in range(len(tst)):
        #print(main2)
        print(main2.loc[i,'d_team'])
        tmp[main2.loc[i,'d_team']]=REG_FILT('data/plstrans/deftrn.csv','data/trans2/deftrn.csv',tst.loc[[i]],100000,None,2,write=False)
    #print(main2['d_team'].value_counts())
    out=pd.DataFrame(columns= ['Team','Spread','Exp','Sharpe'])
    i=0
    for idx,row in main3.iterrows():
        #print(row)
        try:
            dists={}
            dists['home']=tmp[row['home']]
            dists['away']=tmp[row['away']]
            to=row['to']
            nto=[x for x in ('home','away') if x!=to][0]
            print(to)
            #print(dists[to]['d_dif'])
            #print(-int(row['spread']))
            #print(len(dists[to][dists[to]['d_dif']>int(-row['spread'])]))
            #print(len(dists[to][dists[to]['d_dif']>-float(row['spread'])]),len(dists[nto][dists[nto]['d_dif']<float(row['spread'])]))
            predprob=.5*(len(dists[to][dists[to]['d_dif']>-float(row['spread'])])+len(dists[nto][dists[nto]['d_dif']<float(row['spread'])]))/len(dists[to])
            #print(row['odds'][0],row['odds'][1:])
            houseprob=oddtoprob(row['odds'][0],int(row['odds'][1:]))
            if simsharpe(10000,houseprob,predprob)[2]>0:
                print(row,to,predprob,houseprob,predprob/houseprob,simsharpe(10000,houseprob,predprob)) 
                exp,sd,shrp=simsharpe(10000,houseprob,predprob)
                out.loc[i]=[row[to],row['spread'],exp,shrp]
                i+=1
                    #out=pd.DataFrame([to,row['spread']]+simsharpe(10000,row['odds'][0],int(row['odds'][1:]),predprob)[1:3], columns= ['Team','Spread','Exp','Sharpe']) 
            
            #.5*((len(dists[row['to']][dists[row['to']]['d_dif']>row])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist)))
            
        #print('a')
            #oddtoprob(row['odds'])<.5*((len(dists[row['to']][dists[row['to']]['d_dif']>row])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))):

        #print('ayy')
        #print(dectoprob(row['Home Odds Open']),.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))))
        except Exception as e:
            print(e)
                    #print(new['d_dif'].mean(),new['d_dif'].std())
                    #print(main2.loc[[i]][['d_dif','o_team','d_team','o_winpct','d_winpct','d_year','d_week']])
                #new['d_dif'].hist()
                #plt.savefig("plot{0}.pdf".format(str(i)))
                #plt.close()
        #print(yr,wk,wkp,'wkprof')
        #print(yr,wk,wkp/wka,'wkret')
        #cap=wkp
        #print(yr,wk,cap/1000,cap,'netret')
            #totp+=wkp
            #tota+=wka
            #print(yr,wk,totp,'totprof')
            #print(yr,wk,totp/tota,'totret')
        #print(yr,yrp)
        #totp+=yrp
        #print('cum',totp)
    out.to_csv('data/bets/bets.csv')

    home away       date    to spread  odds  year  ssn_start  week
0     TB  HOU 2019-12-21  home     +0  +160  2019 2019-09-05    16
1     TB  HOU 2019-12-21  home   +3.5  -110  2019 2019-09-05    16
2     TB  HOU 2019-12-21  home  +12.5  -360  2019 2019-09-05    16
3     TB  HOU 2019-12-21  home   +9.5  -280  2019 2019-09-05    16
4     TB  HOU 2019-12-21  home   +6.5  -170  2019 2019-09-05    16
..   ...  ...        ...   ...    ...   ...   ...        ...   ...
237  CHI   KC 2019-12-22  away   -3.5  -165  2019 2019-09-05    16
238  CHI   KC 2019-12-22  away   +1.5  -300  2019 2019-09-05    16
239  CHI   KC 2019-12-22  away   +3.5  -450  2019 2019-09-05    16
240  CHI   KC 2019-12-22  away     +0  -270  2019 2019-09-05    16
241  CHI   KC 2019-12-22  away     -6  -115  2019 2019-09-05    16

[242 rows x 9 columns]
ARI


/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


ATL
BAL
BUF
CAR
CHI
CIN
CLE
DAL
DEN
DET
GB
HOU
IND
JAX
KC
LA
LAC
MIA
MIN
NE
NO
NYG
NYJ
OAK
PHI
PIT
SEA
SF
TB
TEN
WAS
home
index                          0
home                          TB
away                         HOU
date         2019-12-21 00:00:00
to                          home
spread                        +0
odds                        +160
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 0, dtype: object home 0.437175 0.38461538461538464 1.136655 (0.12658, 1.2883809621381404, 0.09824733810870148)
home
index                          1
home                          TB
away                         HOU
date         2019-12-21 00:00:00
to                          home
spread                      +3.5
odds                        -110
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 1, dtype: object home 0.554455 0.5238095238095238 1.058505 (0.05305454545454542, 0.9494487

away
index                         47
home                          SF
away                          LA
date         2019-12-21 00:00:00
to                          away
spread                     +15.5
odds                        -390
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 47, dtype: object away 0.85186 0.7959183673469388 1.070285641025641 (0.058274358974358974, 0.4579106243021488, 0.1272614258801453)
home
index                         48
home                         WAS
away                         NYG
date         2019-12-22 00:00:00
to                          home
spread                        +0
odds                        -110
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 48, dtype: object home 0.531525 0.5238095238095238 1.0147295454545455 (0.011436363636363602, 0.9528485972368319, 0.01200228836934634)
home
home
home
index                         51
home 

away
away
away
away
away
home
home
home
home
home
home
home
home
away
away
away
away
away
away
away
away
home
index                        110
home                         CLE
away                         BAL
date         2019-12-22 00:00:00
to                          home
spread                       +10
odds                        -105
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 110, dtype: object home 0.71344 0.5121951219512195 1.3929066666666665 (0.38950952380952386, 0.8843727781203309, 0.44043590377962294)
home
index                        111
home                         CLE
away                         BAL
date         2019-12-22 00:00:00
to                          home
spread                        +0
odds                        +375
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 111, dtype: object home 0.401365 0.21052631578947367 1.9064837500000003 (0.91140

home
home
home
away
index                        168
home                         DEN
away                         DET
date         2019-12-22 00:00:00
to                          away
spread                      -1.5
odds                        +275
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 168, dtype: object away 0.45592 0.26666666666666666 1.7097 (0.7238750000000002, 1.868899738984144, 0.38732682385277045)
away
index                        169
home                         DEN
away                         DET
date         2019-12-22 00:00:00
to                          away
spread                      +1.5
odds                        +225
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 169, dtype: object away 0.51472 0.3076923076923077 1.6728399999999997 (0.662375, 1.624570130642257, 0.4077232416787922)
away
index                        170
home                     

away
away
away
away
away
away
home
home
home
home
home
home
home
home
away
index                        218
home                         SEA
away                         ARI
date         2019-12-22 00:00:00
to                          away
spread                      +1.5
odds                        +280
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 218, dtype: object away 0.38175 0.2631578947368421 1.45065 (0.4516000000000001, 1.8463308045959694, 0.24459322179744666)
away
index                        219
home                         SEA
away                         ARI
date         2019-12-22 00:00:00
to                          away
spread                      +3.5
odds                        +185
year                        2019
ssn_start    2019-09-05 00:00:00
week                          16
Name: 219, dtype: object away 0.479415 0.3508771929824561 1.36633275 (0.358595, 1.4234519226075042, 0.2519192916211173)
away
index   

In [24]:
from pls_filter import *
from customfunctions import *
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

if __name__=="__main__":
    main=pd.read_csv('data/trans1/defense.csv')
    main=main.fillna(0)
    mapdoc=pd.read_excel('data/mapping/team_map.xlsx')
    mapdic={}
    for idx, row in mapdoc.iterrows():
        mapdic[row['oddsteams']]=row['nflscrapr']
    odds=pd.read_csv('data/odds/hist_odds.csv', dtype=str)
    strts=pd.to_datetime(['2009-09-10','2010-09-09','2011-09-08','2012-09-05','2013-09-05','2014-09-04','2015-09-10','2016-09-08','2017-09-07','2018-09-06','2019-09-05','2020-09-05'], format='%Y-%m-%d')
    yrs=[2009,2010,2011,2012,2013,2014,2015,2016,2017,2018,2019]
    bins=pd.IntervalIndex.from_tuples([(strts[i],strts[i+1]) for i in range(len(strts)-1)], closed='left')
    odds['date'] = pd.to_datetime(odds['date'], format='%Y-%m-%d')
    odds=odds[odds['date']>='2009-09-10']
    odds['year']=pd.cut(odds['date'],bins).map(dict(zip(bins,yrs))).astype(int)
    odds['ssn_start']=odds['year'].map(dict(zip(yrs,strts[:-1])))
    odds['week']=((odds['date']-odds['ssn_start']).astype(str).str.split(" ", expand=True)[0].astype(int)//7)+1
    #print(mapdic)
    wk_ret=[]
    print(odds)
    for yr in [2017,2018,2019]:
        for wk in range(1,18):
            totp=0
            tota=0
            cap=1000
            yrp=0
            wkp=0
            wka=0
            main1=main[((main['d_year']>=2011) & (main['d_year']<=yr-1))|((main['d_year']==yr) & (main['d_week']<wk))].reset_index()
            main2=main[((main['d_year']==yr) & (main['d_week']==wk))].reset_index()
            #print(main2)
            main3=odds[((odds['year']==yr) & (odds['week']==wk))].reset_index()
            #print(main3)
            main1.to_csv('data/trans2/deftrn.csv')
            main2.to_csv('data/trans2/deftst.csv')
            yskip=['pass_attempt','complete_pass','air_yards','yards_after_catch','pass_touchdown','complete_pass','air_yards','yards_after_catch','pass_touchdown','rush_attempt','yards_gained','rush_touchdown','sack','interception',
                'fumble_forced','qb_hit','return_touchdown''field_goal_attempt','fg','winpct','dif']
            skip=['o_'+col for col in yskip]
            skip+=['d_'+col for col in yskip]
            y=['d_dif']
            nstnd=['index','d_defteam','d_game_id','d_Game0','d_team','o_defteam','o_game_id','o_Game0','o_team','Unnamed: 0']
            x=[col for col in main.columns if (main[col].dtype==np.float64 or main[col].dtype==np.int64) and col not in nstnd and col not in skip and col not in y]
            #for inp in x:
                #print(inp)
                #stndf=STAND(main,main,stndcols)
            PLS_SAVE(5,'data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav')
            trn=PLS_LTRANS('data/trans2/deftrn.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftrn.csv')
            tst=PLS_LTRANS('data/trans2/deftst.csv','data/trans2/deftrn.csv',x,y,'models/pls/def_sv1.sav','data/plstrans/deftst.csv')
            tmp={}
            #print(tst)
            for i in range(len(tst)):
                #print(main2)
                print(main2.loc[i,'d_team'])
                tmp[main2.loc[i,'d_team']]=REG_FILT('data/plstrans/deftrn.csv','data/trans2/deftrn.csv',tst.loc[[i]],100000,None,2,write=False)
            #print(main2['d_team'].value_counts())
            out=pd.DataFrame(columns= ['Team','Spread','Exp','Sharpe','Prof'])
            i=0
            for idx,row in main3.iterrows():
                #print(row)
                try:
                    dists={}
                    dists['home']=tmp[row['home']]
                    dists['away']=tmp[row['away']]
                    to=row['to']
                    nto=[x for x in ('home','away') if x!=to][0]
                    print(to)
                    #print(dists[to]['d_dif'])
                    #print(-int(row['spread']))
                    #print(len(dists[to][dists[to]['d_dif']>int(-row['spread'])]))
                    #print(len(dists[to][dists[to]['d_dif']>-float(row['spread'])]),len(dists[nto][dists[nto]['d_dif']<float(row['spread'])]))
                    predprob=.5*(len(dists[to][dists[to]['d_dif']>-float(row['spread'])])+len(dists[nto][dists[nto]['d_dif']<float(row['spread'])]))/len(dists[to])
                    #print(row['odds'][0],row['odds'][1:])
                    houseprob=float(row['prob'])
                    if simsharpe(10000,houseprob,predprob)[2]>0:      
                        exp,sd,shrp=simsharpe(10000,houseprob,predprob)
                        amt=cap*shrp/10
                        wka+=amt
                        win=int(row['outcome_bin'])==1
                        prof=betprofit(amt,houseprob,win)
                        print(row,to,predprob,houseprob,predprob/houseprob,simsharpe(10000,houseprob,predprob),prof,int(row['outcome_bin']))
                        wkp+=prof
                        out.loc[i]=[row[to],row['spread'],exp,shrp,prof]
                        i+=1
                            #out=pd.DataFrame([to,row['spread']]+simsharpe(10000,row['odds'][0],int(row['odds'][1:]),predprob)[1:3], columns= ['Team','Spread','Exp','Sharpe']) 

                    #.5*((len(dists[row['to']][dists[row['to']]['d_dif']>row])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist)))

                #print('a')
                    #oddtoprob(row['odds'])<.5*((len(dists[row['to']][dists[row['to']]['d_dif']>row])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))):

                #print('ayy')
                #print(dectoprob(row['Home Odds Open']),.5*((len(homedist[homedist['d_dif']>0])/len(homedist))+(len(awaydist[awaydist['d_dif']<0])/len(awaydist))))
                except Exception as e:
                    print(e)
                            #print(new['d_dif'].mean(),new['d_dif'].std())
                            #print(main2.loc[[i]][['d_dif','o_team','d_team','o_winpct','d_winpct','d_year','d_week']])
                        #new['d_dif'].hist()
                        #plt.savefig("plot{0}.pdf".format(str(i)))
                        #plt.close()
                #print(yr,wk,wkp,'wkprof')
                #print(yr,wk,wkp/wka,'wkret')
                #cap=wkp
                #print(yr,wk,cap/1000,cap,'netret')
                    #totp+=wkp
                    #tota+=wka
                    #print(yr,wk,totp,'totprof')
                    #print(yr,wk,totp/tota,'totret')
                #print(yr,yrp)
                #totp+=yrp
                #print('cum',totp)
            #out.to_csv('data/bets/bets.csv')
            print(wka)
            print(wkp)
            wkret+=[wkp/cap]
            cap+=wkp
            print(cap)

     Unnamed: 0 home away    to       date spread                 prob  \
0             0  SEA  MIN  home 2019-12-02    0.0   0.6024096385542169   
1             1  HOU   NE  home 2019-12-01    0.0   0.4081632653061224   
2             2  DEN  LAC  home 2019-12-01    0.0  0.48780487804878053   
3             3   KC  OAK  home 2019-12-01    0.0    0.819672131147541   
4             4  ARI   LA  home 2019-12-01    0.0  0.36363636363636365   
...         ...  ...  ...   ...        ...    ...                  ...   
6103      12511  NYJ  OAK  away 2014-09-07    5.0   0.5122950819672131   
6104      12512  PHI  JAX  away 2014-09-07   10.0                  0.5   
6105      12513  PIT  CLE  away 2014-09-07    6.0   0.5025125628140703   
6106      12514  STL  MIN  away 2014-09-07    4.0   0.5122950819672131   
6107      12515  SEA   GB  away 2014-09-04    5.0   0.5170630816959669   

     outcome_dif outcome_bin amt  year  ssn_start  week  
0              7           1   0  2019 2019-09-05    

/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


ATL
BAL
BUF
CAR
CHI
CIN
CLE
DAL
DEN
DET
GB
HOU
IND
JAX
KC
LA
LAC
MIN
NE
NO
NYG
NYJ
OAK
PHI
PIT
SEA
SF
TEN
WAS
home
home
home
home
home
index                          715
Unnamed: 0                     715
home                            SF
away                           CAR
to                            home
date           2017-09-10 00:00:00
spread                         0.0
prob            0.3021148036253776
outcome_dif                    -20
outcome_bin                      0
amt                              0
year                          2017
ssn_start      2017-09-07 00:00:00
week                             1
Name: 4, dtype: object home 0.3456 0.3021148036253776 1.143936 (0.1462530000000002, 1.574865546639141, 0.0928669754139412) -8.776286708238825 0
home
home
home
index                          718
Unnamed: 0                     718
home                           CHI
away                           ATL
to                            home
date           2017-09-10 00:00:00
spread

away
index                         2252
Unnamed: 0                    4388
home                            NE
away                            KC
to                            away
date           2017-09-07 00:00:00
spread                         0.0
prob           0.23696682464454977
outcome_dif                     15
outcome_bin                      1
amt                              0
year                          2017
ssn_start      2017-09-07 00:00:00
week                             1
Name: 29, dtype: object away 0.380985 0.23696682464454977 1.6077567000000001 (0.6259659999999998, 2.0537310161859073, 0.30479453982367877) 94.4560360375588 1
home
home
home
home
home
home
home
home
index                         3772
Unnamed: 0                    8044
home                           CHI
away                           ATL
to                            home
date           2017-09-10 00:00:00
spread                         7.0
prob            0.5350454788657036
outcome_dif                

ARI


...

/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


ATL
BAL
BUF
CAR
CHI
CIN
CLE
DAL
DEN
DET
GB
HOU
IND
JAX
KC
LA
LAC
MIA
MIN
NE
NO
NYG
NYJ
OAK
PHI
PIT
SEA
SF
TB
TEN
WAS
0
1000
ARI


/mnt/c/Users/Jeffy/Desktop/agamb/pls_filter.py:82: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  out=comp.ix[D_RESAMP(distances,parts,exp)][ycols]


ATL
BAL
BUF
CAR
CHI
CIN
CLE
DAL
DEN
DET
GB
HOU
IND
JAX
KC
LA
LAC
MIA
MIN
NE
NO
NYG
NYJ
OAK
PHI
PIT
SEA
SF
TB
TEN
WAS
0
1000


ValueError: Found array with 0 sample(s) (shape=(0, 1027)) while a minimum of 1 is required.